In [2]:
import pandas as pd, numpy as np
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn import metrics
import catboost as cb

In [3]:
# 一共有约 500 万条记录，我使用了 1% 的数据：5 万行记录
data = pd.read_csv("./flights/flights.csv")
data = data.sample(frac=0.1, random_state=10)  # 500->50
data = data.sample(frac=0.1, random_state=10)  # 50->5
data.to_csv("./flights/min_flights.csv")

D:\Anoconda\envs\tf1\lib\site-packages\IPython\core\interactiveshell.py:3063: DtypeWarning: Columns (7,8) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [4]:
# 读取 5 万行记录
data = pd.read_csv("./flights/min_flights.csv")
print(data.shape)  # (58191, 31)

data = data[["MONTH", "DAY", "DAY_OF_WEEK", "AIRLINE", "FLIGHT_NUMBER", "DESTINATION_AIRPORT",
             "ORIGIN_AIRPORT", "AIR_TIME", "DEPARTURE_TIME", "DISTANCE", "ARRIVAL_DELAY"]]
data.dropna(inplace=True)

data["ARRIVAL_DELAY"] = (data["ARRIVAL_DELAY"] > 10) * 1

cols = ["AIRLINE", "FLIGHT_NUMBER", "DESTINATION_AIRPORT", "ORIGIN_AIRPORT"]
for item in cols:
    data[item] = data[item].astype("category").cat.codes + 1   ## 所有

train, test, y_train, y_test = train_test_split(data.drop(["ARRIVAL_DELAY"], axis=1), data["ARRIVAL_DELAY"],
                                                random_state=10, test_size=0.25)

cat_features_index = [0, 1, 2, 3, 4, 5, 6]

(58191, 32)


In [5]:
data

MONTH  DAY  DAY_OF_WEEK  AIRLINE  FLIGHT_NUMBER  DESTINATION_AIRPORT  \
0          6   25            4        4           2109                  272   
1         11   21            6       13           1912                  426   
2          5   21            4        1           1217                  338   
3          5   12            2       14            732                  529   
4          2   20            5       14           4710                  301   
...      ...  ...          ...      ...            ...                  ...   
58186      8   17            1       14            384                  447   
58187      4    4            6       14           3735                  513   
58188     12   16            3       14            235                  513   
58189      1   21            3       10           5393                  530   
58190      4    5            7        9            143                  338   

       ORIGIN_AIRPORT  AIR_TIME  DEPARTURE_TIME  DISTANCE  ARRIVAL_DELAY  
0                 315     142.0           846.0      1184              1  
1                 516      60.0          2103.0       414              0  
2                 351     173.0           556.0      1313              0  
3                 435     244.0          1448.0      1733              0  
4                 355     155.0          1504.0      1165              0  
...               ...       ...             ...       ...            ...  
58186             264     111.0          2021.0       591              1  
58187             414      56.0          2051.0       345              0  
58188             416      65.0          2143.0       391              0  
58189             524      89.0           644.0       599              1  
58190             264     125.0          1122.0       731              0  

[57140 rows x 11 columns]

In [6]:
def auc(m, train, test):
    return (metrics.roc_auc_score(y_train, m.predict_proba(train)[:, 1]),
            metrics.roc_auc_score(y_test, m.predict_proba(test)[:, 1]))
# 调参，用网格搜索调出最优参数
params = {'depth': [4, 7, 10],
          'learning_rate': [0.03, 0.1, 0.15],
          'l2_leaf_reg': [1, 4, 9],
          'iterations': [300, 500]}
ccatb = cb.CatBoostClassifier()
cb_model = GridSearchCV(ccatb, params, scoring="roc_auc", cv=3)
cb_model.fit(train, y_train)
# 查看最佳分数
print(cb_model.best_score_)  # 0.7088001891107445
# 查看最佳参数
print(cb_model.best_params_)  # {'depth': 4, 'iterations': 500, 'l2_leaf_reg': 9, 'learning_rate': 0.15}

0:	learn: 0.6816980	total: 90ms	remaining: 26.9s
1:	learn: 0.6709708	total: 103ms	remaining: 15.3s
2:	learn: 0.6606130	total: 116ms	remaining: 11.5s
3:	learn: 0.6512554	total: 129ms	remaining: 9.53s
4:	learn: 0.6424092	total: 141ms	remaining: 8.31s
5:	learn: 0.6341715	total: 156ms	remaining: 7.62s
6:	learn: 0.6265202	total: 168ms	remaining: 7.04s
7:	learn: 0.6193048	total: 180ms	remaining: 6.58s
8:	learn: 0.6124975	total: 194ms	remaining: 6.29s
9:	learn: 0.6061685	total: 208ms	remaining: 6.03s
10:	learn: 0.6004243	total: 224ms	remaining: 5.89s
11:	learn: 0.5948909	total: 237ms	remaining: 5.7s
12:	learn: 0.5898243	total: 252ms	remaining: 5.56s
13:	learn: 0.5849259	total: 266ms	remaining: 5.42s
14:	learn: 0.5806101	total: 279ms	remaining: 5.3s
15:	learn: 0.5763598	total: 295ms	remaining: 5.23s
16:	learn: 0.5723536	total: 308ms	remaining: 5.12s
17:	learn: 0.5685149	total: 324ms	remaining: 5.07s
18:	learn: 0.5648646	total: 337ms	remaining: 4.98s
19:	learn: 0.5616839	total: 350ms	remaining:

174:	learn: 0.4942893	total: 2.61s	remaining: 1.86s
175:	learn: 0.4942276	total: 2.62s	remaining: 1.84s
176:	learn: 0.4941664	total: 2.63s	remaining: 1.83s
177:	learn: 0.4941378	total: 2.65s	remaining: 1.81s
178:	learn: 0.4940392	total: 2.66s	remaining: 1.8s
179:	learn: 0.4939617	total: 2.67s	remaining: 1.78s
180:	learn: 0.4939062	total: 2.69s	remaining: 1.77s
181:	learn: 0.4938576	total: 2.7s	remaining: 1.75s
182:	learn: 0.4938031	total: 2.71s	remaining: 1.73s
183:	learn: 0.4936618	total: 2.73s	remaining: 1.72s
184:	learn: 0.4935288	total: 2.74s	remaining: 1.7s
185:	learn: 0.4934742	total: 2.75s	remaining: 1.69s
186:	learn: 0.4934354	total: 2.76s	remaining: 1.67s
187:	learn: 0.4933909	total: 2.78s	remaining: 1.66s
188:	learn: 0.4933039	total: 2.79s	remaining: 1.64s
189:	learn: 0.4932602	total: 2.81s	remaining: 1.63s
190:	learn: 0.4931719	total: 2.82s	remaining: 1.61s
191:	learn: 0.4930731	total: 2.84s	remaining: 1.6s
192:	learn: 0.4929948	total: 2.85s	remaining: 1.58s
193:	learn: 0.49

42:	learn: 0.5192672	total: 569ms	remaining: 3.4s
43:	learn: 0.5182566	total: 587ms	remaining: 3.41s
44:	learn: 0.5175685	total: 600ms	remaining: 3.4s
45:	learn: 0.5167983	total: 613ms	remaining: 3.38s
46:	learn: 0.5161800	total: 624ms	remaining: 3.36s
47:	learn: 0.5153762	total: 640ms	remaining: 3.36s
48:	learn: 0.5147064	total: 653ms	remaining: 3.35s
49:	learn: 0.5141443	total: 665ms	remaining: 3.33s
50:	learn: 0.5133969	total: 680ms	remaining: 3.32s
51:	learn: 0.5127808	total: 695ms	remaining: 3.31s
52:	learn: 0.5122204	total: 707ms	remaining: 3.3s
53:	learn: 0.5117720	total: 723ms	remaining: 3.29s
54:	learn: 0.5112289	total: 736ms	remaining: 3.28s
55:	learn: 0.5107974	total: 752ms	remaining: 3.27s
56:	learn: 0.5103481	total: 766ms	remaining: 3.26s
57:	learn: 0.5099565	total: 781ms	remaining: 3.26s
58:	learn: 0.5094904	total: 796ms	remaining: 3.25s
59:	learn: 0.5089205	total: 815ms	remaining: 3.26s
60:	learn: 0.5085729	total: 831ms	remaining: 3.26s
61:	learn: 0.5080911	total: 845ms	

206:	learn: 0.4887158	total: 2.89s	remaining: 1.3s
207:	learn: 0.4886296	total: 2.91s	remaining: 1.29s
208:	learn: 0.4885420	total: 2.92s	remaining: 1.27s
209:	learn: 0.4884786	total: 2.94s	remaining: 1.26s
210:	learn: 0.4884098	total: 2.95s	remaining: 1.24s
211:	learn: 0.4883429	total: 2.96s	remaining: 1.23s
212:	learn: 0.4882935	total: 2.97s	remaining: 1.21s
213:	learn: 0.4881971	total: 2.98s	remaining: 1.2s
214:	learn: 0.4881606	total: 2.99s	remaining: 1.18s
215:	learn: 0.4881041	total: 3s	remaining: 1.17s
216:	learn: 0.4880728	total: 3.02s	remaining: 1.15s
217:	learn: 0.4879676	total: 3.03s	remaining: 1.14s
218:	learn: 0.4879080	total: 3.04s	remaining: 1.13s
219:	learn: 0.4878787	total: 3.06s	remaining: 1.11s
220:	learn: 0.4877781	total: 3.07s	remaining: 1.1s
221:	learn: 0.4877183	total: 3.08s	remaining: 1.08s
222:	learn: 0.4876377	total: 3.1s	remaining: 1.07s
223:	learn: 0.4875661	total: 3.12s	remaining: 1.06s
224:	learn: 0.4875118	total: 3.13s	remaining: 1.04s
225:	learn: 0.48740

68:	learn: 0.5075679	total: 925ms	remaining: 3.1s
69:	learn: 0.5071938	total: 938ms	remaining: 3.08s
70:	learn: 0.5068272	total: 947ms	remaining: 3.05s
71:	learn: 0.5065034	total: 962ms	remaining: 3.05s
72:	learn: 0.5061852	total: 977ms	remaining: 3.04s
73:	learn: 0.5058687	total: 989ms	remaining: 3.02s
74:	learn: 0.5056959	total: 1s	remaining: 3s
75:	learn: 0.5054281	total: 1.01s	remaining: 2.99s
76:	learn: 0.5051079	total: 1.03s	remaining: 2.97s
77:	learn: 0.5048936	total: 1.04s	remaining: 2.97s
78:	learn: 0.5046973	total: 1.05s	remaining: 2.95s
79:	learn: 0.5045669	total: 1.07s	remaining: 2.93s
80:	learn: 0.5044144	total: 1.08s	remaining: 2.93s
81:	learn: 0.5041974	total: 1.09s	remaining: 2.91s
82:	learn: 0.5040467	total: 1.11s	remaining: 2.9s
83:	learn: 0.5038773	total: 1.12s	remaining: 2.88s
84:	learn: 0.5036422	total: 1.14s	remaining: 2.87s
85:	learn: 0.5034846	total: 1.15s	remaining: 2.86s
86:	learn: 0.5033350	total: 1.16s	remaining: 2.85s
87:	learn: 0.5031615	total: 1.18s	remai

...

362:	learn: 0.2185674	total: 17.1s	remaining: 6.45s
363:	learn: 0.2183794	total: 17.1s	remaining: 6.4s
364:	learn: 0.2178267	total: 17.2s	remaining: 6.36s
365:	learn: 0.2172390	total: 17.2s	remaining: 6.31s
366:	learn: 0.2171375	total: 17.3s	remaining: 6.26s
367:	learn: 0.2168061	total: 17.3s	remaining: 6.21s
368:	learn: 0.2163274	total: 17.4s	remaining: 6.17s
369:	learn: 0.2160949	total: 17.4s	remaining: 6.12s
370:	learn: 0.2157108	total: 17.5s	remaining: 6.07s
371:	learn: 0.2153217	total: 17.5s	remaining: 6.03s
372:	learn: 0.2150021	total: 17.6s	remaining: 5.98s
373:	learn: 0.2146648	total: 17.6s	remaining: 5.93s
374:	learn: 0.2142678	total: 17.6s	remaining: 5.88s
375:	learn: 0.2139533	total: 17.7s	remaining: 5.84s
376:	learn: 0.2135978	total: 17.7s	remaining: 5.79s
377:	learn: 0.2133763	total: 17.8s	remaining: 5.74s
378:	learn: 0.2129406	total: 17.8s	remaining: 5.7s
379:	learn: 0.2126566	total: 17.9s	remaining: 5.65s
380:	learn: 0.2123294	total: 17.9s	remaining: 5.6s
381:	learn: 0.2

27:	learn: 0.5013592	total: 392ms	remaining: 6.6s
28:	learn: 0.5010019	total: 407ms	remaining: 6.61s
29:	learn: 0.5005441	total: 422ms	remaining: 6.61s
30:	learn: 0.5002747	total: 439ms	remaining: 6.64s
31:	learn: 0.4996589	total: 452ms	remaining: 6.61s
32:	learn: 0.4993894	total: 465ms	remaining: 6.58s
33:	learn: 0.4989139	total: 480ms	remaining: 6.57s
34:	learn: 0.4985209	total: 494ms	remaining: 6.57s
35:	learn: 0.4983383	total: 509ms	remaining: 6.56s
36:	learn: 0.4981810	total: 524ms	remaining: 6.56s
37:	learn: 0.4978997	total: 539ms	remaining: 6.55s
38:	learn: 0.4976028	total: 553ms	remaining: 6.54s
39:	learn: 0.4971443	total: 566ms	remaining: 6.51s
40:	learn: 0.4969087	total: 581ms	remaining: 6.5s
41:	learn: 0.4965272	total: 596ms	remaining: 6.5s
42:	learn: 0.4963490	total: 605ms	remaining: 6.43s
43:	learn: 0.4959700	total: 620ms	remaining: 6.42s
44:	learn: 0.4957356	total: 634ms	remaining: 6.41s
45:	learn: 0.4953773	total: 649ms	remaining: 6.41s
46:	learn: 0.4949434	total: 664ms	

194:	learn: 0.4715668	total: 2.82s	remaining: 4.41s
195:	learn: 0.4714738	total: 2.83s	remaining: 4.39s
196:	learn: 0.4714139	total: 2.85s	remaining: 4.38s
197:	learn: 0.4713224	total: 2.86s	remaining: 4.36s
198:	learn: 0.4712239	total: 2.87s	remaining: 4.35s
199:	learn: 0.4711333	total: 2.89s	remaining: 4.33s
200:	learn: 0.4710379	total: 2.9s	remaining: 4.32s
201:	learn: 0.4709562	total: 2.92s	remaining: 4.3s
202:	learn: 0.4707524	total: 2.93s	remaining: 4.29s
203:	learn: 0.4706299	total: 2.94s	remaining: 4.27s
204:	learn: 0.4705237	total: 2.96s	remaining: 4.25s
205:	learn: 0.4704560	total: 2.97s	remaining: 4.24s
206:	learn: 0.4703407	total: 2.98s	remaining: 4.22s
207:	learn: 0.4702019	total: 3s	remaining: 4.21s
208:	learn: 0.4701454	total: 3.01s	remaining: 4.2s
209:	learn: 0.4700757	total: 3.03s	remaining: 4.18s
210:	learn: 0.4699839	total: 3.04s	remaining: 4.16s
211:	learn: 0.4699060	total: 3.05s	remaining: 4.15s
212:	learn: 0.4698321	total: 3.07s	remaining: 4.13s
213:	learn: 0.4696

356:	learn: 0.4584197	total: 5.14s	remaining: 2.06s
357:	learn: 0.4583357	total: 5.16s	remaining: 2.04s
358:	learn: 0.4582558	total: 5.17s	remaining: 2.03s
359:	learn: 0.4581897	total: 5.19s	remaining: 2.02s
360:	learn: 0.4581027	total: 5.2s	remaining: 2s
361:	learn: 0.4580303	total: 5.22s	remaining: 1.99s
362:	learn: 0.4579515	total: 5.23s	remaining: 1.97s
363:	learn: 0.4578861	total: 5.24s	remaining: 1.96s
364:	learn: 0.4578336	total: 5.26s	remaining: 1.94s
365:	learn: 0.4577812	total: 5.27s	remaining: 1.93s
366:	learn: 0.4577344	total: 5.29s	remaining: 1.92s
367:	learn: 0.4576612	total: 5.3s	remaining: 1.9s
368:	learn: 0.4575913	total: 5.32s	remaining: 1.89s
369:	learn: 0.4574564	total: 5.33s	remaining: 1.87s
370:	learn: 0.4573721	total: 5.35s	remaining: 1.86s
371:	learn: 0.4573325	total: 5.36s	remaining: 1.84s
372:	learn: 0.4572603	total: 5.38s	remaining: 1.83s
373:	learn: 0.4572117	total: 5.39s	remaining: 1.82s
374:	learn: 0.4571591	total: 5.41s	remaining: 1.8s
375:	learn: 0.45710

AttributeError: 'CatBoostClassifier' object has no attribute 'CatBoostClassifier'

In [ ]:
# Without Categorical features，用最优参数拟合数据(最优参数由上面得到，此处要进行修改)
clf = cb.CatBoostClassifier(eval_metric="AUC", depth=4, iterations=500, l2_leaf_reg=9,
                            learning_rate=0.15)
clf.fit(train, y_train)
print(auc(clf, train, test))  # (0.7809684655761157, 0.7104617034553192)

In [ ]:
# with categorical features
clf = cb.CatBoostClassifier(eval_metric="AUC", one_hot_max_size=31, depth=4, iterations=500, l2_leaf_reg=9,
                            learning_rate=0.15)
clf.fit(train, y_train, cat_features=cat_features_index)
print(auc(clf, train, test))  # (0.7817912095285117, 0.7152541135019913)